# Chicago ETL Gold Layer

Cargando Configuración de Secretos

In [0]:
service_credential = dbutils.secrets.get(scope="secret_scope",key="adlskey")
app_id = dbutils.secrets.get(scope="secret_scope",key="appclient")
tenant_id = dbutils.secrets.get(scope="secret_scope",key="directorytenant")


spark.conf.set("fs.azure.account.auth.type.chicagotaxiadls.dfs.core.windows.net", "OAuth")
spark.conf.set("fs.azure.account.oauth.provider.type.chicagotaxiadls.dfs.core.windows.net", "org.apache.hadoop.fs.azurebfs.oauth2.ClientCredsTokenProvider")
spark.conf.set("fs.azure.account.oauth2.client.id.chicagotaxiadls.dfs.core.windows.net", app_id)
spark.conf.set("fs.azure.account.oauth2.client.secret.chicagotaxiadls.dfs.core.windows.net", service_credential)
spark.conf.set("fs.azure.account.oauth2.client.endpoint.chicagotaxiadls.dfs.core.windows.net", "https://login.microsoftonline.com/{0}/oauth2/token".format(tenant_id))

Cargando Información del Silver Layer

In [0]:
chicago_taxi_silver_df = spark.read.format("parquet").load("abfss://silver@chicagotaxiadls.dfs.core.windows.net/taxi_data")

### Resumir Información Relevante para crear el Gold Layer

Realizare la Operacion de Agrupar por las columnas month, trip_start_date, trip_end_date, taxi_id, payment_id, company para obtener el numero total de viajes, el promedio de trip_seconds y trip_miles, el total de trip_seconds, trip_miles, fare, tips, tolls, extras, trip_total

In [0]:
from pyspark.sql.functions import *

chicago_taxi_gold_df = chicago_taxi_silver_df.groupBy("month", "trip_start_date", "trip_end_date", "taxi_id", "pickup_community_area", "dropoff_community_area", "payment_id", "company") \
        .agg(
                count(col("*")).alias("trips"), \
                avg("trip_seconds").alias("avg_trip_seconds"), \
                avg("trip_miles").alias("avg_trip_miles"), \
                sum("trip_seconds").alias("trip_seconds"), \
                sum("trip_miles").alias("trip_miles"), \
                sum("fare").alias("fare"), \
                sum("tips").alias("tips"), \
                sum("tolls").alias("tolls"), \
                sum("extras").alias("extras"), \
                sum("trip_total").alias("trip_total") \
        )

In [0]:
display(chicago_taxi_gold_df)

month trip_start_date trip_end_date taxi_id pickup_community_area dropoff_community_area payment_id company trips avg_trip_seconds avg_trip_miles trip_seconds trip_miles fare tips tolls extras trip_total 6 2016-06-18 2016-06-18 1513 999 999 2 999 2 900.0 2.0 1800 4.0 20.5 6.12 0.0 3.5 31.12 6 2016-06-23 2016-06-23 6509 32 33 2 109 1 540.0 2.5 540 2.5 9.75 2.0 0.0 0.0 11.75 6 2016-06-05 2016-06-05 3646 28 7 2 999 1 540.0 3.0 540 3.0 10.25 2.0 0.0 0.0 12.75 6 2016-06-13 2016-06-13 4051 8 76 2 101 2 2220.0 17.35 4440 34.7 86.5 17.5 0.0 1.0 105.0 6 2016-06-08 2016-06-08 5894 32 8 2 109 1 420.0 1.1 420 1.1 6.75 2.0 0.0 0.0 8.75 6 2016-06-17 2016-06-17 7384 32 1 2 999 1 240.0 1.2 240 1.2 6.5 1.0 0.0 0.0 8.0 6 2016-06-09 2016-06-09 4005 32 32 2 999 1 180.0 0.2 180 0.2 4.0 0.8 0.0 0.0 5.3 6 2016-06-30 2016-07-01 6129 76 8 2 101 1 1380.0 17.2 1380 17.2 42.25 10.45 0.0 10.0 62.7 6 2016-06-19 2016-06-19 2485 25 28 2 999 1 1380.0 3.1 1380 3.1 10.75 3.0 0.0 0.0 14.25 6 2016-06-03 2016-06-03 4694 32 8 2 999 1 720.0 1.6 720 1.6 9.0 3.0 0.0 0.0 12.5 6 2016-06-08 2016-06-08 4984 7 56 2 107 1 1800.0 0.9 1800 0.9 39.0 9.75 0.0 0.0 48.75 6 2016-06-20 2016-06-20 8034 8 32 2 109 1 900.0 1.2 900 1.2 9.0 1.0 0.0 0.0 10.0 6 2016-06-03 2016-06-03 881 6 32 2 109 1 720.0 5.1 720 5.1 16.0 4.0 0.0 0.0 20.0 6 2016-06-22 2016-06-22 5379 32 39 2 101 1 840.0 6.6 840 6.6 19.0 2.0 0.0 0.0 21.0 6 2016-06-09 2016-06-09 6892 8 8 2 107 2 360.0 0.7 720 1.4 11.75 3.0 0.0 0.0 14.75 6 2016-06-09 2016-06-09 3885 32 28 2 999 2 1440.0 1.3 2880 2.6 24.5 6.4 0.0 0.0 31.9 6 2016-06-24 2016-06-24 7012 8 32 2 107 1 600.0 1.5 600 1.5 8.0 1.0 0.0 0.0 9.0 6 2016-06-14 2016-06-14 516 32 8 2 999 2 600.0 1.2000000000000002 1200 2.4000000000000004 15.25 5.0 0.0 0.0 21.25 6 2016-06-19 2016-06-19 1445 8 7 2 101 2 420.0 1.6500000000000001 840 3.3000000000000003 15.25 5.5 0.0 0.5 21.25 6 2016-06-15 2016-06-15 3790 999 999 2 999 18 815.8888888888889 2.8122222222222213 14686 50.61999999999998 201.5 48.61 0.0 7.0 266.11 6 2016-06-21 2016-06-21 6728 3 8 2 999 1 780.0 6.1 780 6.1 18.0 4.5 0.0 0.0 23.0 6 2016-06-08 2016-06-08 6961 8 32 2 999 3 500.0 1.2333333333333334 1500 3.7 22.0 4.7 0.0 0.0 28.2 6 2016-06-03 2016-06-03 685 999 999 2 999 6 1390.0 7.533333333333334 8340 45.2 133.75 32.07 0.0 15.5 184.31999999999996 6 2016-06-09 2016-06-09 4788 8 28 2 10 1 780.0 2.9 780 2.9 11.5 0.5 0.0 0.0 12.0 6 2016-06-07 2016-06-07 6875 999 999 2 999 10 1560.0 7.739999999999999 15600 77.39999999999999 230.5 53.99999999999999 0.0 12.0 301.5 6 2016-06-28 2016-06-28 6726 28 32 2 107 2 540.0 2.15 1080 4.3 18.5 3.45 0.0 0.0 21.95 6 2016-06-24 2016-06-24 662 7 8 2 107 1 720.0 0.1 720 0.1 9.5 2.2 0.0 1.5 13.2 6 2016-06-18 2016-06-18 7750 6 28 2 107 1 1500.0 7.5 1500 7.5 23.75 0.25 0.0 1.0 25.0 6 2016-06-14 2016-06-14 986 8 28 2 107 1 600.0 1.2 600 1.2 8.0 2.0 0.0 2.0 12.0 6 2016-06-22 2016-06-22 1854 7 6 2 107 1 1080.0 1.6 1080 1.6 10.5 2.1 0.0 0.0 12.6 6 2016-06-10 2016-06-10 5170 76 999 2 999 1 1920.0 19.6 1920 19.6 48.0 36.0 0.0 4.0 88.5 6 2016-06-23 2016-06-23 6877 76 6 2 999 1 2040.0 14.4 2040 14.4 37.0 8.2 0.0 4.0 49.7 6 2016-06-22 2016-06-22 4621 76 8 2 107 1 3660.0 17.0 3660 17.0 46.25 5.0 0.0 5.0 56.25 6 2016-06-19 2016-06-19 3525 8 7 2 109 3 500.0 2.733333333333333 1500 8.2 25.75 4.5 0.0 1.0 31.25 6 2016-06-27 2016-06-27 2082 76 32 2 109 2 2610.0 17.75 5220 35.5 91.0 22.45 0.0 9.0 122.45 6 2016-06-13 2016-06-13 1630 8 999 2 109 1 1320.0 14.6 1320 14.6 35.75 7.15 0.0 0.0 42.9 6 2016-06-13 2016-06-13 7589 999 999 2 999 8 1372.5 7.1000000000000005 10980 56.800000000000004 175.0 40.18 0.0 16.5 235.68 6 2016-06-28 2016-06-28 2870 32 32 2 107 2 210.0 0.6499999999999999 420 1.2999999999999998 9.75 5.0 0.0 1.5 16.25 6 2016-06-13 2016-06-13 5294 76 999 2 107 1 1320.0 11.5 1320 11.5 29.5 12.05 0.0 18.75 60.3 6 2016-06-27 2016-06-27 6111 8 8 2 999 1 420.0 0.8 420 0.8 6.0 1.5 0.0 0.0 8.0 6 2016-06-08 2016-06-08 368 32 8 2 107 2 780.0 1.85 1560 3.7 18.25 6.15 0.0 2.0 26.4 6 2016-06-06 2016-06-06 542 77 32 2 43 1 540.

### Guardando Informacion en ADLS

In [0]:
chicago_taxi_gold_df.write  \
        .partitionBy("month") \
        .mode("overwrite")  \
        .format("parquet")  \
        .save("abfss://gold@chicagotaxiadls.dfs.core.windows.net/taxi_data")